In [2]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer
import torch
DEVICE = torch.device("cuda:0")

model_name_or_path = "sberbank-ai/rugpt3small_based_on_gpt2"
tokenizer = GPT2Tokenizer.from_pretrained(model_name_or_path)
model = GPT2LMHeadModel.from_pretrained(model_name_or_path).to(DEVICE)

In [3]:
with open('anekdoty.txt', 'r', encoding='utf-8') as file:
    text = file.read()

In [4]:
from transformers import TextDataset, DataCollatorForLanguageModeling

# Сохраним обучающие данные в .txt файл 
train_path = 'train_dataset.txt'
with open(train_path, "w") as f:
    f.write(text)

# Создание датасета
train_dataset = TextDataset(tokenizer=tokenizer,file_path=train_path,block_size=32)
  
# Создание даталодера (нарезает текст на оптимальные по длине куски)
data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=False)

/home/polyakovk/venv_linux/lib/python3.11/site-packages/transformers/data/datasets/language_modeling.py:53: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(


In [5]:
from transformers import Trainer, TrainingArguments

training_args = TrainingArguments(
    output_dir="./finetuned",
    overwrite_output_dir=True,
    num_train_epochs=30,
    per_device_train_batch_size=32,
    per_device_eval_batch_size=16,
    warmup_steps=10,
    gradient_accumulation_steps=32,
    )

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
    optimizers = (torch.optim.AdamW(model.parameters(),lr=0.001),None)
)

In [5]:
trainer.train()

TrainOutput(global_step=240, training_loss=0.9343911488850911, metrics={'train_runtime': 4515.8084, 'train_samples_per_second': 58.428, 'train_steps_per_second': 0.053, 'total_flos': 4011240960000000.0, 'train_loss': 0.9343911488850911, 'epoch': 27.927272727272726})

In [9]:
model_path = "finetuned"
tokenizer = GPT2Tokenizer.from_pretrained(model_path)
model = GPT2LMHeadModel.from_pretrained(model_path).to(DEVICE)

In [70]:
def generate_jokes(prompt, temperature, top_p, max_length, num_return_sequences):
    input_ids = tokenizer.encode(prompt, return_tensors='pt').to(DEVICE)
    
    # Генерируем несколько шуток
    outputs = model.generate(
        input_ids=input_ids,
        do_sample=True,
        # num_beams=5,
        temperature=temperature,
        top_p=top_p,
        max_length=max_length,
        num_return_sequences=num_return_sequences
    )
    
    # Обработка всех сгенерированных шуток
    jokes = []
    for output in outputs:
        generated_text = tokenizer.decode(output, skip_special_tokens=True)
        # Обрезаем текст после первой точки
        if '…' in generated_text:
            generated_text = generated_text.split('…')[0] + '.'
        elif '.' in generated_text:
            generated_text = generated_text.split('.')[0] + '.'
        elif '!' in generated_text:
            generated_text = generated_text.split('!')[0] + '.'
        jokes.append(generated_text)
    
    return jokes

In [73]:
text = "Шла Саша по шоссе"
print(generate_jokes(text, 1, 0.9, 30, 4))

['Шла Саша по шоссе, громко разговаривая с шофером.', 'Шла Саша по шоссе, громко матерясь и упирая руку в ширинку.', 'Шла Саша по шоссе, несла пургу и, как раз, дождь.', 'Шла Саша по шоссе, но не за трактором.']


In [10]:
text = "однажды я пришел из школы"
input_ids = tokenizer.encode(text, return_tensors="pt").to(DEVICE)
model.eval()
with torch.no_grad():
    out = model.generate(input_ids, 
                        do_sample=True,
                        num_beams=2,
                        temperature=1.5,
                        top_p=0.9,
                        max_length=30,
                        
                        )

generated_text = list(map(tokenizer.decode, out))[0]
print()
print(generated_text)


однажды я проваливал экзамен по истории.
— Вино с возрастом становится лучше. Я становлюсь лучше с вином…
— Сними


In [8]:
# model.save_pretrained('./finetuned')
# tokenizer.save_pretrained('./finetuned')

In [38]:
# import requests
# from bs4 import BeautifulSoup
# import re

# # Функция для получения шуток с одной страницы
# def get_jokes_from_page(url):
#     response = requests.get(url, headers=headers)
#     response.raise_for_status()  # Проверка на ошибки запроса

#     soup = BeautifulSoup(response.text, 'html.parser')

#     # Находим все анекдоты на странице
#     jokes = soup.find_all('div', class_='anekdot-text')  # Замените селектор на правильный

#     page_jokes = []
#     for joke in jokes:
#         # Извлекаем текст анекдота
#         joke_text = joke.get_text(strip=True)
        
#         # Удаляем цифры и символы в конце текста
#         joke_text_cleaned = re.sub(r'\d+[\#\d]*$', '', joke_text).strip()
        
#         # Добавляем очищенный текст в список
#         page_jokes.append(joke_text_cleaned)
    
#     return page_jokes

# # URL-шаблон для страниц
# base_url = "https://anekdotovstreet.com/korotkie-anekdoty/{}/"

# # Заголовки для имитации браузера
# headers = {
#     'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36'
# }

# # Открываем файл для записи анекдотов
# with open('anekdoty.txt', 'w', encoding='utf-8') as file:
#     for page_number in range(2, 400):
#         # Формируем URL для текущей страницы
#         url = base_url.format(page_number)
#         print(f"Собираю шутки со страницы {page_number}...")

#         # Получаем шутки с текущей страницы
#         jokes = get_jokes_from_page(url)
        
#         # Если шуток нет, значит, страницы закончились (опционально)
#         if not jokes:
#             print(f"Шутки на странице {page_number} не найдены.")
#             continue
        
#         # Записываем шутки в файл
#         for joke in jokes:
#             file.write(joke + '\n')

# print("Анекдоты успешно сохранены в файл 'anekdoty.txt'.")